In [ ]:
import numpy as np
import pandas as pd

%matplotlib inline

In [ ]:
from voting_methods import *

# "jugement majoritaire"

## test with fake data

In [ ]:
from faker import Faker


Faker.seed("voting")
ff = Faker("fr")

In [ ]:
candidates = [ff.first_name() for _ in range(8)]

In [ ]:
elect = MajorityJudgement(candidates)

In [ ]:
elect.add_candidate("Manu")

###  create random votes

In [ ]:
import numpy as np


NAMES = elect.get_candidates()
NOTES = elect.notes

np.random.seed(123456789)


def get_random_vote(names=NAMES, notes=NOTES):
    return {name: np.random.choice(notes) for name in names}


def get_random_variation(vote, notes=NOTES, changes=2):
    """Get a variation of the vote"""
    vote = vote.copy()
    names = list(vote.keys())
    for _ in range(changes):
        vote[np.random.choice(names)] = np.random.choice(notes)
    return vote
    

In [ ]:
all_votes = []

for _ in range(5):
    init_vote = get_random_vote()  # general opinion
    all_votes.extend([get_random_variation(init_vote) for _ in range(50)])

In [ ]:
for vote in all_votes:
    elect.vote(vote)

In [ ]:
elect.results

In [ ]:
elect.get_mentions("Manu")

In [ ]:
elect.get_winner()

### visualization of results

In [ ]:
elect.results.style.background_gradient()

In [ ]:
elect.plot(figsize=(10, 6), fontsize=15)

In [ ]:
elect.get_majority_mentions()

In [ ]:
elect.get_best_candidates()

# Condorcet 

## tests 

transform previous votes to preference lists

In [ ]:
test_vote = np.random.choice(all_votes)
test_vote

In [ ]:
jm_to_order(test_vote)

In [ ]:
elect = Condorcet()
for vote in map(jm_to_order, all_votes):
    elect.vote(vote)

In [ ]:
duel_mat = elect.get_duel_matrix()
duel_mat

In [ ]:
duel_mat.style.background_gradient(axis=0)

In [ ]:
elect.plot()

In [ ]:
elect.get_winner()

# Borda

In [ ]:
elect = Borda()

In [ ]:
def borda_vote(borda):
    for vote in map(jm_to_order, all_votes):
        borda.vote(vote)
        
borda_vote(elect)

In [ ]:
elect.plot(figsize=(10, 6), fontsize=15)

In [ ]:
point_variations = {
    "traditional": [8, 7, 6, 5, 4, 3, 2, 1, 0],
    "formula1": [25, 18, 15, 12, 10, 8, 6, 4, 2],
    "supermario kart": [9, 6, 3, 1, 0, 0, 0, 0, 0],
    "mariokart 8": [15, 12, 10, 9, 8, 7, 6, 5, 4],
}

In [ ]:
results = {}

for k, v in point_variations.items():
    elect = Borda()
    elect.points = list(v)
    borda_vote(elect)
    results[k] = elect.get_results()

In [ ]:
comparision_matrix = pd.DataFrame(results).sort_values('traditional', ascending=False)
comparision_matrix.style.background_gradient()

In [ ]:
comparision_matrix.plot(kind="bar", figsize=(10, 6), fontsize=15)

In [ ]:
comparision_matrix.apply(lambda x: x / max(x)).plot(kind="bar", figsize=(10, 6), fontsize=15)

# Approval voting

In [ ]:
jm_to_approval(all_votes[0])

In [ ]:
all_votes[0]

In [ ]:
approval = Approval()

In [ ]:
for vote in all_votes:
    approval.vote(jm_to_approval(vote))

In [ ]:
approval.get_results()

In [ ]:
approval.plot(figsize=(10, 6), fontsize=15)